In [1]:
import random
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import Lasso
from sklearn.model_selection import train_test_split, GridSearchCV
from collections import Counter


In [2]:
CSV_FILE_PATH = '../Datasets/AllForSelection.csv'
# load the training dataset
lesion = pd.read_csv(CSV_FILE_PATH, usecols=lambda x: 'Unnamed' not in x)

# Display a random sample of 10 observations
sample = lesion.sample(10)

print(f"Shape of data: {sample.shape}")
sample


Shape of data: (10, 103)


original_firstorder_10Percentile  original_firstorder_90Percentile  \
12908                              75.0                             152.0   
13641                              53.0                             132.0   
52913                              58.0                             181.0   
24997                              58.0                             112.0   
41957                              58.0                             142.0   
42330                              44.0                             139.0   
22144                             118.0                             167.0   
59645                              65.0                             151.0   
53988                             105.0                             152.0   
30116                             128.0                             175.0   

       original_firstorder_Energy  original_firstorder_Entropy  \
12908                1.502670e+09                     2.220455   
13641                6.884669e+07                     2.111914   
52913                5.401298e+08                     2.754624   
24997                2.736846e+08                     1.656319   
41957                1.584886e+09                     2.323502   
42330                4.620820e+08                     2.415175   
22144                3.453438e+08                     1.644295   
59645                1.189686e+09                     2.319200   
53988                2.426678e+09                     1.612530   
30116                3.686644e+09                     1.693054   

       original_firstorder_InterquartileRange  original_firstorder_Kurtosis  \
12908                                    49.0                      1.918522   
13641                                    54.0                      1.718948   
52913                                    67.0                      2.114529   
24997                                    32.0                      2.220062   
41957                                    49.0                      2.209721   
42330                                    66.0                      1.698705   
22144                                    24.0                      4.165411   
59645                                    54.0                      2.066112   
53988                                    27.0                      2.354507   
30116                                    24.0                      3.347157   

       original_firstorder_Maximum  original_firstorder_Mean  \
12908                        177.0                115.322764   
13641                        153.0                 89.889871   
52913                        210.0                112.509978   
24997                        146.0                 80.848471   
41957                        176.0                103.386435   
42330                        162.0                 89.717536   
22144                        204.0                146.974380   
59645                        185.0                114.272102   
53988                        187.0                127.322933   
30116                        203.0                153.044718   

       original_firstorder_MeanAbsoluteDeviation  original_firstorder_Median  \
12908                                  24.687316                       119.0   
13641                                  26.017294                        87.0   
52913                                  37.147589                       105.0   
24997                                  17.456572                        75.0   
41957                                  26.042004                       107.0   
42330                                  31.482037                        88.0   
22144                                  15.774099                       153.0   
59645                                  27.561094                       121.0   
53988                                  14.421584                       126.0   
30116                                  14.563061         

In [3]:
lesion[['categories']] = lesion[['categories']].astype(int)


In [4]:
lesion


original_firstorder_10Percentile  original_firstorder_90Percentile  \
0                                  77.0                             162.0   
1                                  64.0                              96.0   
2                                  73.0                             137.0   
3                                 120.0                             191.0   
4                                  76.0                             145.0   
...                                 ...                               ...   
60073                             128.0                             175.0   
60074                              61.0                             144.0   
60075                             104.0                             171.0   
60076                              18.0                             151.0   
60077                              60.0                             157.0   

       original_firstorder_Energy  original_firstorder_Entropy  \
0                    1.518163e+08                     2.290459   
1                    4.267857e+08                     1.232669   
2                    4.726186e+08                     1.934125   
3                    2.589335e+09                     2.010853   
4                    1.410037e+09                     2.085313   
...                           ...                          ...   
60073                3.244814e+09                     1.792354   
60074                4.935057e+08                     2.208266   
60075                7.804357e+08                     2.041734   
60076                3.880729e+08                     2.763355   
60077                1.750154e+09                     2.490992   

       original_firstorder_InterquartileRange  original_firstorder_Kurtosis  \
0                                        48.0                      2.351248   
1                                        17.0                      3.429680   
2                                        37.0                      2.073204   
3                                        43.0                      2.473451   
4                                        35.0                      2.470766   
...                                       ...                           ...   
60073                                    18.0                      7.000809   
60074                                    58.0                      1.709141   
60075                                    37.0                      2.670836   
60076                                    93.0                      1.708051   
60077                                    64.0                      1.939287   

       original_firstorder_Maximum  original_firstorder_Mean  \
0                            215.0                127.408673   
1                            154.0                 80.481700   
2                            156.0                105.831695   
3                            213.0                159.546304   
4                            171.0                112.160795   
...                            ...                       ...   
60073                        207.0                151.505775   
60074                        161.0                104.141212   
60075                        190.0                140.606658   
60076                        206.0                 76.926250   
60077                        200.0                103.942467   

       original_firstorder_MeanAbsoluteDeviation  original_firstorder_Median  \
0                                      26.461359                       135.0   
1                                      10.097202                        81.0   
2                                      19.355369                       106.0   
3                                      22.837109                       165.0   
4                                      20.342325                       114.0   
...                                          ...                         ...   
60073      

In [5]:
lesion_label = 'categories'

column_names = lesion.columns.tolist()

feature_names = column_names[:-1]

lesion_label = column_names[-1]


In [6]:
pipeline = Pipeline([
                     ('scaler',StandardScaler()),
                     ('model',Lasso())
])

search = GridSearchCV(pipeline,
                      {'model__alpha':np.arange(0.1,10,0.1)},
                      cv = 5, scoring="neg_mean_squared_error",verbose=3
                      )


In [7]:
lesion_X, lesion_y = lesion[feature_names].values, lesion[lesion_label].values

temp = list(zip(lesion_X, lesion_y))
random.shuffle(temp)
res1, res2 = zip(*temp)
# res1 and res2 come out as tuples, and so must be converted to lists.
lesion_X, lesion_y = list(res1), list(res2)  


In [8]:
Counter(lesion_y)

Counter({1: 40230, 0: 6672, 4: 6588, 2: 3084, 3: 1962, 6: 852, 5: 690})

In [9]:
search.fit(lesion_X,lesion_y)
search.best_params_
coefficients = search.best_estimator_.named_steps['model'].coef_
importance = np.abs(coefficients)
np.array(feature_names)[importance > 0]


Fitting 5 folds for each of 99 candidates, totalling 495 fits
[CV 1/5] END .................model__alpha=0.1;, score=-1.377 total time=   0.5s
[CV 2/5] END .................model__alpha=0.1;, score=-1.365 total time=   0.5s
[CV 3/5] END .................model__alpha=0.1;, score=-1.444 total time=   0.5s
[CV 4/5] END .................model__alpha=0.1;, score=-1.378 total time=   0.4s
[CV 5/5] END .................model__alpha=0.1;, score=-1.350 total time=   0.5s
[CV 1/5] END .................model__alpha=0.2;, score=-1.425 total time=   0.3s
[CV 2/5] END .................model__alpha=0.2;, score=-1.419 total time=   0.3s
[CV 3/5] END .................model__alpha=0.2;, score=-1.492 total time=   0.3s
[CV 4/5] END .................model__alpha=0.2;, score=-1.420 total time=   0.3s
[CV 5/5] END .................model__alpha=0.2;, score=-1.394 total time=   0.2s
[CV 1/5] END .model__alpha=0.30000000000000004;, score=-1.494 total time=   0.2s
[CV 2/5] END .model__alpha=0.30000000000000004;

array(['original_firstorder_10Percentile',
       'original_firstorder_RootMeanSquared', 'original_glcm_MCC'],
      dtype='<U50')

In [16]:
search = GridSearchCV(pipeline,
                      {'model__alpha':np.arange(0.001,10,0.001)},
                      cv = 5, scoring="neg_mean_squared_error",verbose=3
                      )

search.fit(lesion_X,lesion_y)
search.best_params_
coefficients = search.best_estimator_.named_steps['model'].coef_
importance = np.abs(coefficients)
np.array(feature_names)[importance > 0]


Fitting 5 folds for each of 9999 candidates, totalling 49995 fits


/Users/krystian/anaconda3/envs/Main/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.541e+03, tolerance: 1.560e+00
  model = cd_fast.enet_coordinate_descent(


[CV 1/5] END ...............model__alpha=0.001;, score=-2.583 total time=   0.4s


/Users/krystian/anaconda3/envs/Main/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.483e+03, tolerance: 1.529e+00
  model = cd_fast.enet_coordinate_descent(


[CV 2/5] END ...............model__alpha=0.001;, score=-2.673 total time=   0.4s


...

[CV 5/5] END ...............model__alpha=0.006;, score=-2.538 total time=   0.3s
[CV 1/5] END ...............model__alpha=0.007;, score=-2.771 total time=   0.3s
[CV 2/5] END ...............model__alpha=0.007;, score=-2.839 total time=   0.3s


/Users/krystian/anaconda3/envs/Main/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.710e+00, tolerance: 1.536e+00
  model = cd_fast.enet_coordinate_descent(


[CV 3/5] END ...............model__alpha=0.007;, score=-2.807 total time=   0.4s
[CV 4/5] END ...............model__alpha=0.007;, score=-2.489 total time=   0.3s
[CV 5/5] END ...............model__alpha=0.007;, score=-2.556 total time=   0.2s
[CV 1/5] END ...............model__alpha=0.008;, score=-2.781 total time=   0.2s
[CV 2/5] END ...............model__alpha=0.008;, score=-2.856 total time=   0.2s
[CV 3/5] END ...............model__alpha=0.008;, score=-2.814 total time=   0.4s
[CV 4/5] END ...............model__alpha=0.008;, score=-2.505 total time=   0.2s
[CV 5/5] END ...............model__alpha=0.008;, score=-2.567 total time=   0.3s
[CV 1/5] END model__alpha=0.009000000000000001;, score=-2.793 total time=   0.2s
[CV 2/5] END model__alpha=0.009000000000000001;, score=-2.868 total time=   0.1s
[CV 3/5] END model__alpha=0.009000000000000001;, score=-2.827 total time=   0.1s
[CV 4/5] END model__alpha=0.009000000000000001;, score=-2.523 total time=   0.2s
[CV 5/5] END model__alpha=0.

/Users/krystian/anaconda3/envs/Main/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.108e+03, tolerance: 1.932e+00
  model = cd_fast.enet_coordinate_descent(


array(['original_firstorder_10Percentile',
       'original_firstorder_90Percentile', 'original_firstorder_Energy',
       'original_firstorder_Entropy',
       'original_firstorder_InterquartileRange',
       'original_firstorder_Kurtosis', 'original_firstorder_Maximum',
       'original_firstorder_Mean',
       'original_firstorder_MeanAbsoluteDeviation',
       'original_firstorder_Median', 'original_firstorder_Minimum',
       'original_firstorder_RobustMeanAbsoluteDeviation',
       'original_firstorder_RootMeanSquared',
       'original_firstorder_Skewness', 'original_firstorder_Uniformity',
       'original_firstorder_Variance', 'original_glcm_ClusterProminence',
       'original_glcm_ClusterShade', 'original_glcm_Contrast',
       'original_glcm_DifferenceAverage',
       'original_glcm_DifferenceEntropy', 'original_glcm_Imc2',
       'original_glcm_InverseVariance', 'original_glcm_JointAverage',
       'original_glcm_JointEntropy', 'original_glcm_MCC',
       'original_glcm_Ma

In [17]:
search = GridSearchCV(pipeline,
                      {'model__alpha':np.arange(0.1,100,0.1)},
                      cv = 5, scoring="neg_mean_squared_error",verbose=3
                      )

search.fit(lesion_X,lesion_y)
search.best_params_
coefficients = search.best_estimator_.named_steps['model'].coef_
importance = np.abs(coefficients)
np.array(feature_names)[importance > 0]


Fitting 5 folds for each of 999 candidates, totalling 4995 fits
[CV 1/5] END .................model__alpha=0.1;, score=-2.998 total time=   0.0s
[CV 2/5] END .................model__alpha=0.1;, score=-3.085 total time=   0.0s
[CV 3/5] END .................model__alpha=0.1;, score=-3.115 total time=   0.0s
[CV 4/5] END .................model__alpha=0.1;, score=-2.818 total time=   0.0s
[CV 5/5] END .................model__alpha=0.1;, score=-2.916 total time=   0.0s
[CV 1/5] END .................model__alpha=0.2;, score=-3.047 total time=   0.0s
[CV 2/5] END .................model__alpha=0.2;, score=-3.171 total time=   0.0s
[CV 3/5] END .................model__alpha=0.2;, score=-3.208 total time=   0.0s
[CV 4/5] END .................model__alpha=0.2;, score=-2.919 total time=   0.0s
[CV 5/5] END .................model__alpha=0.2;, score=-3.014 total time=   0.0s
[CV 1/5] END .model__alpha=0.30000000000000004;, score=-3.111 total time=   0.0s
[CV 2/5] END .model__alpha=0.3000000000000000

array(['original_firstorder_90Percentile', 'original_firstorder_Minimum',
       'original_glcm_Idmn',
       'original_gldm_SmallDependenceLowGrayLevelEmphasis',
       'original_glrlm_RunEntropy', 'original_shape2D_Elongation',
       'original_shape2D_MaximumDiameter', 'original_shape2D_Sphericity'],
      dtype='<U50')

In [18]:
search = GridSearchCV(pipeline,
                      {'model__alpha':np.arange(0.01,10,0.01)},
                      cv = 5, scoring="neg_mean_squared_error",verbose=3
                      )

search.fit(lesion_X,lesion_y)
search.best_params_
coefficients = search.best_estimator_.named_steps['model'].coef_
importance = np.abs(coefficients)
np.array(feature_names)[importance > 0]


Fitting 5 folds for each of 999 candidates, totalling 4995 fits
[CV 1/5] END ................model__alpha=0.01;, score=-2.802 total time=   0.1s
[CV 2/5] END ................model__alpha=0.01;, score=-2.883 total time=   0.1s
[CV 3/5] END ................model__alpha=0.01;, score=-2.839 total time=   0.2s
[CV 4/5] END ................model__alpha=0.01;, score=-2.540 total time=   0.2s
[CV 5/5] END ................model__alpha=0.01;, score=-2.585 total time=   0.2s
[CV 1/5] END ................model__alpha=0.02;, score=-2.883 total time=   0.1s
[CV 2/5] END ................model__alpha=0.02;, score=-2.975 total time=   0.0s
[CV 3/5] END ................model__alpha=0.02;, score=-2.917 total time=   0.1s
[CV 4/5] END ................model__alpha=0.02;, score=-2.646 total time=   0.0s
[CV 5/5] END ................model__alpha=0.02;, score=-2.674 total time=   0.1s
[CV 1/5] END ................model__alpha=0.03;, score=-2.907 total time=   0.0s
[CV 2/5] END ................model__alpha=0.0

array(['original_firstorder_90Percentile', 'original_firstorder_Energy',
       'original_firstorder_Kurtosis', 'original_firstorder_Maximum',
       'original_firstorder_Median', 'original_firstorder_Minimum',
       'original_firstorder_Skewness', 'original_firstorder_TotalEnergy',
       'original_firstorder_Variance', 'original_glcm_ClusterProminence',
       'original_glcm_ClusterShade', 'original_glcm_DifferenceVariance',
       'original_glcm_Imc2', 'original_glcm_MaximumProbability',
       'original_gldm_DependenceEntropy',
       'original_gldm_DependenceVariance',
       'original_gldm_GrayLevelNonUniformity',
       'original_gldm_LargeDependenceLowGrayLevelEmphasis',
       'original_glrlm_HighGrayLevelRunEmphasis',
       'original_glrlm_LongRunLowGrayLevelEmphasis',
       'original_glrlm_RunEntropy',
       'original_glrlm_RunLengthNonUniformity',
       'original_glrlm_RunVariance',
       'original_glszm_HighGrayLevelZoneEmphasis',
       'original_glszm_LargeAreaLowG

In [19]:
search = GridSearchCV(pipeline,
                      {'model__alpha':np.arange(0.1,10,0.1)},
                      cv = 5, scoring="neg_mean_squared_error",verbose=3
                      )

search.fit(lesion_X,lesion_y)
search.best_params_
coefficients = search.best_estimator_.named_steps['model'].coef_
importance = np.abs(coefficients)
np.array(feature_names)[importance > 0]


Fitting 5 folds for each of 99 candidates, totalling 495 fits
[CV 1/5] END .................model__alpha=0.1;, score=-2.998 total time=   0.0s
[CV 2/5] END .................model__alpha=0.1;, score=-3.085 total time=   0.0s
[CV 3/5] END .................model__alpha=0.1;, score=-3.115 total time=   0.0s
[CV 4/5] END .................model__alpha=0.1;, score=-2.818 total time=   0.0s
[CV 5/5] END .................model__alpha=0.1;, score=-2.916 total time=   0.0s
[CV 1/5] END .................model__alpha=0.2;, score=-3.047 total time=   0.0s
[CV 2/5] END .................model__alpha=0.2;, score=-3.171 total time=   0.0s
[CV 3/5] END .................model__alpha=0.2;, score=-3.208 total time=   0.0s
[CV 4/5] END .................model__alpha=0.2;, score=-2.919 total time=   0.0s
[CV 5/5] END .................model__alpha=0.2;, score=-3.014 total time=   0.0s
[CV 1/5] END .model__alpha=0.30000000000000004;, score=-3.111 total time=   0.0s
[CV 2/5] END .model__alpha=0.30000000000000004;

array(['original_firstorder_90Percentile', 'original_firstorder_Minimum',
       'original_glcm_Idmn',
       'original_gldm_SmallDependenceLowGrayLevelEmphasis',
       'original_glrlm_RunEntropy', 'original_shape2D_Elongation',
       'original_shape2D_MaximumDiameter', 'original_shape2D_Sphericity'],
      dtype='<U50')